Source:
Github of Isabel Segura Bedmar 
https://github.com/isegura/BasicNLP

- TextClassification
https://github.com/turmovasiring/TextClassification/blob/master/SpamDetection.ipynb

Source: Resources for "Natural Language Processing" Coursera course. https://www.coursera.org/learn/language-processing
- week1-MultilabelClassification.ipynb 
https://github.com/hse-aml/natural-language-processing/blob/master/week1/week1-MultilabelClassification.ipynb


## Connect Drive


In [1]:
from google.colab import drive
drive.mount("/content/drive/")
!ls

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive/
drive  sample_data


# Import libraries

In [44]:
!pip install -U scikit-learn
!pip install sklearn

import sklearn
print('The scikit-learn version is {}.'.format(sklearn.__version__))

#dataframes
import pandas as pd
from tabulate import tabulate
import numpy as np

#regex
import re

#models
import spacy

import re
import ast
import tqdm
import pickle
import collections
import numpy as np
import scipy as sp
import pandas as pd

import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stopwords_en = stopwords.words("english")
nltk.download('punkt')
from nltk import word_tokenize
from nltk.stem.porter import PorterStemmer

from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC
from sklearn.neural_network import MLPClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import MultinomialNB

from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.metrics import f1_score, make_scorer
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix
from sklearn.pipeline import Pipeline
from sklearn.multiclass import OneVsRestClassifier

import warnings
warnings.simplefilter(action='ignore', category=DeprecationWarning)
warnings.simplefilter(action='ignore', category=FutureWarning)

import ast
from ast import literal_eval

#Grader
import sys
sys.path.append('/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2')
import grader
from grader import Grader
grader = Grader()

Requirement already up-to-date: scikit-learn in /usr/local/lib/python3.6/dist-packages (0.22.2.post1)
The scikit-learn version is 0.22.2.post1.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


#Input

###Input from source

Data source :
https://zenodo.org/record/3693570#.Xo-JAfFS8_-   > version 1.2 10.5281/zenodo.3693570 	Jan 23, 2020 

Colaboratory folder : Codiespv2/datasetv3/

>T1. train/text_files/... (Articles, Diagnostics/Procedures, train)

>T2. dev/text_files/...  (Articles, Diagnostics/Procedures, dev)

>T3. test/text_files/... (Articles, Diagnostics/Procedures, test)

>T4. train/text_files_en/... (Articles, Diagnostics/Procedures, train, english)

>T5. dev/text_files_en/... (Articles, Diagnostics/Procedures, dev, english)

>T6. test/text_files_en/... (Articles, Diagnostics/Procedures, test, english)

>A1. train/trainD.tsv (Annotations, Diagnostics, train)

>A2. dev/devD.tsv (Annotations, Diagnostics, dev)

>A3. train/trainP.tsv (Annotations, Procedures, train)

>A4. dev/devP.tsv (Annotations, Procedures, dev)

###Input from other Notebook

In the notebook **"2104_Crear tsv a partir de text files v3.ipynb"**, there is a section called **"Create a tsv from all text files"**. It is necessary to execute it before load the independent text files.

https://colab.research.google.com/drive/1qlZ8aPBbsAWmOFOn0QwKa-9S8E8Pt0-A#scrollTo=WG8ULg0lrCA6

datasetv3:

>T1. train/text_files/...  --> train/train_articles_codiesp.csv

>T2. dev/text_files/...  --> dev/dev_articles_codiesp.csv

>T3. test/text_files/...  --> test/test_articles_codiesp.csv

>T4. train/text_files_en/...  --> train/train_articles_en_codiesp.csv

>T5. dev/text_files_en/...  --> dev/dev_articles_en_codiesp.csv

>T6. test/text_files_en/...  --> test/test_articles_en_codiesp.csv

###Total input

>T1. datasetv3/train/train_articles_codiesp.csv (Articles, Diagnostics/Procedures, train)

>T2. datasetv3/dev/dev_articles_codiesp.csv (Articles, Diagnostics/Procedures, dev)

>T3. datasetv3/test/test_articles_codiesp.csv (Articles, Diagnostics/Procedures, test)

>T4. datasetv3/train/train_articles_en_codiesp.csv (Articles, Diagnostics/Procedures, train, english)

>T5. datasetv3/dev/dev_articles_en_codiesp.csv (Articles, Diagnostics/Procedures, dev, english)

>T6. datasetv3/test/test_articles_en_codiesp.csv (Articles, Diagnostics/Procedures, test, english)

>A1. datasetv3/train/trainD.tsv (Annotations, Diagnostics, train)

>A2. datasetv3/dev/devD.tsv (Annotations, Diagnostics, dev)

>A3. datasetv3/train/trainP.tsv (Annotations, Procedures, train)

>A4. datasetv3/dev/devP.tsv (Annotations, Procedures, dev)

#Load data

In [0]:
path_codiesp='/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/'

path_T1 = path_codiesp + 'datasetv3/train/train_articles_codiesp.csv'
path_T2 = path_codiesp + 'datasetv3/dev/dev_articles_codiesp.csv'
path_T3 = path_codiesp + 'datasetv3/test/test_articles_codiesp.csv'
path_T4 = path_codiesp + 'datasetv3/train/train_articles_en_codiesp.csv'
path_T5 = path_codiesp + 'datasetv3/dev/dev_articles_en_codiesp.csv'
path_T6 = path_codiesp + 'datasetv3/test/test_articles_en_codiesp.csv'

path_A1 = path_codiesp + 'datasetv3/train/trainD.tsv'
path_A2 = path_codiesp + 'datasetv3/dev/devD.tsv'
path_A3 = path_codiesp + 'datasetv3/train/trainP.tsv'
path_A4 = path_codiesp + 'datasetv3/dev/devP.tsv'

path_B1 = path_codiesp + 'datasetv3/train/mapped_annotations/trainD_annotations_mapped'
path_B2 = path_codiesp + 'datasetv3/dev/mapped_annotations/devD_annotations_mapped'
path_B3 = path_codiesp + 'datasetv3/train/mapped_annotations/trainP_annotations_mapped'
path_B4 = path_codiesp + 'datasetv3/dev/mapped_annotations/devP_annotations_mapped'

path_C1 = path_codiesp + 'codiesp_codesv2/codiesp-D_codes.tsv'
path_C2 = path_codiesp + 'codiesp_codesv2/codiesp-P_codes.tsv'

path_J1 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/articles_annotated/train_annotated_articles_D.csv'
path_J2 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/articles_annotated/dev_annotated_articles_D.csv'
path_J3 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/articles_annotated/train_annotated_articles_en_D.csv'
path_J4 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/articles_annotated/dev_annotated_articles_en_D.csv'

path_J5= '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/articles_annotated/train_annotated_articles_P.csv'
path_J6 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/articles_annotated/dev_annotated_articles_P.csv'
path_J7 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/articles_annotated/train_annotated_articles_en_P.csv'
path_J8 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/articles_annotated/dev_annotated_articles_en_P.csv'

path_K1 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/K_mapped_annotated_articles/trainD_mapped_annotated_articles.csv'
path_K2 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/K_mapped_annotated_articles/devD_mapped_annotated_articles.csv'
path_K3 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/K_mapped_annotated_articles/trainD_mapped_annotated_articles_en.csv'
path_K4 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/K_mapped_annotated_articles/devD_mapped_annotated_articles_en.csv'

path_K5= '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/K_mapped_annotated_articles/trainP_mapped_annotated_articles.csv'
path_K6 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/K_mapped_annotated_articles/devP_mapped_annotated_articles.csv'
path_K7 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/K_mapped_annotated_articles/trainP_mapped_annotated_articles_en.csv'
path_K8 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/K_mapped_annotated_articles/devP_mapped_annotated_articles_en.csv'


>T1. Articles, Diagnostics/Procedures, train

>T2. Articles, Diagnostics/Procedures, dev

>T3. Articles, Diagnostics/Procedures, test

>T4. Articles, Diagnostics/Procedures, train, english

>T5. Articles, Diagnostics/Procedures, dev, english

>T6. Articles, Diagnostics/Procedures, test, english

>A1. Annotations, Diagnostics, train

>A2. Annotations, Diagnostics, dev

>A3. Annotations, Procedures, train

>A4. Annotations, Procedures, dev

>B1. Mapped_annotations, Diagnostics, train

>B2.Mapped_annotations, Diagnostics, dev

>B3. Mapped_annotations, Procedures, train

>B4. Mapped_annotations, Procedures, dev

##Load articles from tsv (train/dev/test & es/en)

In [4]:
def load_articles(path):
  df = pd.read_csv(path, sep=",", engine="python", encoding='utf-8')
  print("--- Loaded dataset:", path)

  print("--- Number of rows is " + str(df.shape[0]) + " x number of columns " + str(df.shape[1]))
  #print(df.head())
  #print(tabulate(df.head(), headers='keys', tablefmt='psql'))

  return df

path_codiesp='/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/'

print("- Load T1. Articles, Diagnostics/Procedures, train")
train_file_articles = path_codiesp + 'datasetv3/train/train_articles_codiesp.csv'
df_train_articles = load_articles(train_file_articles)

print("- Load T2. Articles, Diagnostics/Procedures, dev")
dev_file_articles = path_codiesp + 'datasetv3/dev/dev_articles_codiesp.csv'
df_dev_articles = load_articles(dev_file_articles)

#print("- Load T3. Articles, Diagnostics/Procedures, test")
#test_file_articles = path_codiesp + 'datasetv3/test/test_articles_codiesp.csv'
#df_test_articles = load_articles(test_file_articles)

print("- Load T4. Articles, Diagnostics/Procedures, train, english")
train_file_articles_en = path_codiesp + 'datasetv3/train/train_articles_en_codiesp.csv'
df_train_articles_en = load_articles(train_file_articles_en)

print("- Load T5. Articles, Diagnostics/Procedures, dev, english")
dev_file_articles_en = path_codiesp + 'datasetv3/dev/dev_articles_en_codiesp.csv'
df_dev_articles_en = load_articles(dev_file_articles_en)

#print("- Load T6. Articles, Diagnostics/Procedures, test, english")
#test_file_articles_en = path_codiesp + 'datasetv3/test/test_articles_en_codiesp.csv'
#df_test_articles_en = load_articles(test_file_articles_en)

- Load T1. Articles, Diagnostics/Procedures, train
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/train_articles_codiesp.csv
--- Number of rows is 500 x number of columns 2
- Load T2. Articles, Diagnostics/Procedures, dev
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/dev_articles_codiesp.csv
--- Number of rows is 250 x number of columns 2
- Load T4. Articles, Diagnostics/Procedures, train, english
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/train_articles_en_codiesp.csv
--- Number of rows is 500 x number of columns 2
- Load T5. Articles, Diagnostics/Procedures, dev, english
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/dev_articles_en_codiesp.csv
--- Number of rows is 250 x number of columns 2


##Loading annotations from tsv (train/dev, D/P)

In [5]:
def load_data(path, names):
  df = pd.read_csv(path, sep="\t", names=names)
  print("--- Loaded dataset:", path)

  print("--- Number of rows is " + str(df.shape[0]) + " x number of columns " + str(df.shape[1]))
  #print(df.head())
  #print(tabulate(df.head(), headers='keys', tablefmt='psql'))

  return df

path_codiesp='/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/'
names_annotations=["ArticleID", "ICD10-code",]  #Columns: articleID \t  ICD10-code 

print("- Load A1. Annotations, Diagnostics, train")
file_train_annotationsD = path_codiesp + 'datasetv3/train/trainD.tsv'
df_train_annotationsD = load_data(file_train_annotationsD, names_annotations)

print("- Load A2. Annotations, Diagnostics, dev")
file_dev_annotationsD = path_codiesp + 'datasetv3/dev/devD.tsv'
df_dev_annotationsD = load_data(file_dev_annotationsD, names_annotations)

print("- Load A3. Annotations, Procedures, train")
file_train_annotationsP = path_codiesp + 'datasetv3/train/trainP.tsv'
df_train_annotationsP = load_data(file_train_annotationsP, names_annotations)

print("- Load A4. Annotations, Procedures, dev")
file_dev_annotationsP = path_codiesp + 'datasetv3/dev/devP.tsv'
df_dev_annotationsP = load_data(file_dev_annotationsP, names_annotations)

- Load A1. Annotations, Diagnostics, train
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/trainD.tsv
--- Number of rows is 5639 x number of columns 2
- Load A2. Annotations, Diagnostics, dev
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/devD.tsv
--- Number of rows is 2677 x number of columns 2
- Load A3. Annotations, Procedures, train
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/trainP.tsv
--- Number of rows is 1550 x number of columns 2
- Load A4. Annotations, Procedures, dev
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/devP.tsv
--- Number of rows is 817 x number of columns 2


##Load annotations with easier tags from tsv(train/dev, D/P)

In [6]:
def load_data(path):
  df = pd.read_csv(path, sep=",")
  print("--- Loaded dataset:", path)

  print("--- Number of rows is " + str(df.shape[0]) + " x number of columns " + str(df.shape[1]))
  #print(df.head())
  #print(tabulate(df.head(), headers='keys', tablefmt='psql'))

  return df

path_codiesp='/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/'

print("- Load B1. Mapped annotations, Diagnostics, train")
path = path_codiesp + 'datasetv3/train/mapped_annotations/trainD_annotations_mapped'
df_trainD_annotations_mapping = load_data(path)

print("- Load B2. Mapped annotations, Diagnostics, dev")
path = path_codiesp + 'datasetv3/dev/mapped_annotations/devD_annotations_mapped'
df_devD_annotations_mapping  = load_data(path)

print("-  Load B3. Mapped annotations, Procedures, train")
path = path_codiesp + 'datasetv3/train/mapped_annotations/trainP_annotations_mapped'
df_trainP_annotations_mapping = load_data(path)

print("- Load B4. Mapped annotations, Procedures, dev")
path = path_codiesp + 'datasetv3/dev/mapped_annotations/devP_annotations_mapped'
df_devP_annotations_mapping  = load_data(path)


- Load B1. Mapped annotations, Diagnostics, train
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/mapped_annotations/trainD_annotations_mapped
--- Number of rows is 5639 x number of columns 2
- Load B2. Mapped annotations, Diagnostics, dev
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/mapped_annotations/devD_annotations_mapped
--- Number of rows is 2677 x number of columns 2
-  Load B3. Mapped annotations, Procedures, train
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/mapped_annotations/trainP_annotations_mapped
--- Number of rows is 1550 x number of columns 2
- Load B4. Mapped annotations, Procedures, dev
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/mapped_annotations/devP_annotations_mapped
--- Number of rows is 817 x number of columns 2


In [7]:
print("- Print B1. Mapped annotations, Diagnostics, train")
print(tabulate(df_trainD_annotations_mapping.head(), headers='keys', tablefmt='psql'))

print("- Print B2. Mapped annotations, Diagnostics, dev")
print(tabulate(df_devD_annotations_mapping.head(), headers='keys', tablefmt='psql'))

print("- Print B3. Mapped annotations, Procedures, train")
print(tabulate(df_trainP_annotations_mapping.head(), headers='keys', tablefmt='psql'))   

print("- Print B4. Mapped annotations, Procedures, dev")
print(tabulate(df_devP_annotations_mapping.head(), headers='keys', tablefmt='psql'))

- Print B1. Mapped annotations, Diagnostics, train
+----+---------------------------+---------------+
|    | article_id                |   mapped_tags |
|----+---------------------------+---------------|
|  0 | S0004-06142005000700014-1 |         23621 |
|  1 | S0004-06142005000700014-1 |         96956 |
|  2 | S0004-06142005000700014-1 |         29039 |
|  3 | S0004-06142005000700014-1 |         29009 |
|  4 | S0004-06142005000700014-1 |           181 |
+----+---------------------------+---------------+
- Print B2. Mapped annotations, Diagnostics, dev
+----+---------------------------+---------------+
|    | article_id                |   mapped_tags |
|----+---------------------------+---------------|
|  0 | S0004-06142005000900016-1 |         27975 |
|  1 | S0004-06142005000900016-1 |         23479 |
|  2 | S0004-06142005000900016-1 |         23560 |
|  3 | S0004-06142005000900016-1 |         28751 |
|  4 | S0004-06142005000900016-1 |         23453 |
+----+---------------------------

>B1. datasetv3/train/mapped_annotations/trainD_annotations_mapped.tsv (Mapped_annotations, Diagnostics, train)

>B2. datasetv3/dev/mapped_annotations/devD_annotations_mapped.tsv (Mapped_annotations, Diagnostics, dev)

>B3. datasetv3/train/mapped_annotations/trainP_annotations_mapped.tsv (Mapped_annotations, Procedures, train)

>B4. datasetv3/dev/mapped_annotations/devP_annotations_mapped.tsv (Mapped_annotations, Procedures, dev)

##Loading codes from tsv (D/P)

In [16]:
def load_data(path, names):
  df = pd.read_csv(path, sep="\t", names=names)
  print("--- Loaded dataset:", path)

  print("--- Number of rows is " + str(df.shape[0]) + " x number of columns " + str(df.shape[1]))
  #print(df.head())
  #print(tabulate(df.head(), headers='keys', tablefmt='psql'))

  return df

#It uses load_data(path, names)
 
path_codiesp='/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/'
names_codeD=["Code", "Es-description", "En-description"]   # Columns: code \t es-description \t en-description
names_codeP=["Code", "Es-description", "En-description"]   # Columns: code \t es-description \t en-description \t approach?

print("- Load C1. Codes, Diagnostics")
file_codeD = path_codiesp + 'codiesp_codesv2/codiesp-D_codes.tsv'
df_codeD = load_data(file_codeD, names_codeD)

print("- Load C2. Codes, Procedures")
file_codeP = path_codiesp + 'codiesp_codesv2/codiesp-P_codes.tsv'
df_codeP = load_data(file_codeP, names_codeP)



- Load C1. Codes, Diagnostics
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/codiesp_codesv2/codiesp-D_codes.tsv
--- Number of rows is 98288 x number of columns 3
- Load C2. Codes, Procedures
--- Loaded dataset: /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/codiesp_codesv2/codiesp-P_codes.tsv
--- Number of rows is 87170 x number of columns 3


##Load K articles annotated with easier tags from tsv(train/dev, D/P)

In [0]:
path_J1 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/articles_annotated/train_annotated_articles_D.csv'
path_J2 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/articles_annotated/dev_annotated_articles_D.csv'
path_J3 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/articles_annotated/train_annotated_articles_en_D.csv'
path_J4 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/articles_annotated/dev_annotated_articles_en_D.csv'

path_J5= '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/articles_annotated/train_annotated_articles_P.csv'
path_J6 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/articles_annotated/dev_annotated_articles_P.csv'
path_J7 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/articles_annotated/train_annotated_articles_en_P.csv'
path_J8 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/articles_annotated/dev_annotated_articles_en_P.csv'

path_K1 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/K_mapped_annotated_articles/trainD_mapped_annotated_articles.csv'
path_K2 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/K_mapped_annotated_articles/devD_mapped_annotated_articles.csv'
path_K3 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/K_mapped_annotated_articles/trainD_mapped_annotated_articles_en.csv'
path_K4 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/K_mapped_annotated_articles/devD_mapped_annotated_articles_en.csv'

path_K5= '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/K_mapped_annotated_articles/trainP_mapped_annotated_articles.csv'
path_K6 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/K_mapped_annotated_articles/devP_mapped_annotated_articles.csv'
path_K7 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/K_mapped_annotated_articles/trainP_mapped_annotated_articles_en.csv'
path_K8 = '/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/K_mapped_annotated_articles/devP_mapped_annotated_articles_en.csv'


In [23]:
def read_data(filename):
    data = pd.read_csv(filename, sep=',', usecols=["article_content", "tags"])
    #print(data['tags'])
    #print(data['article_content'])
    return data


path_codiesp='/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/'

print("- Read K3. Joined, Mapped, Diagnostics, train, english")
trainD_en = read_data(path_K3)
print("- Read K4. Joined, Mapped, Diagnostics, dev, english")
devD_en = read_data(path_K4)



print('Shape of data')
print(f'Train: {trainD_en.shape}')
print(f'Validation: {devD_en.shape}')

- Read K3. Joined, Mapped, Diagnostics, train, english
- Read K4. Joined, Mapped, Diagnostics, dev, english
Shape of data
Train: (500, 2)
Validation: (250, 2)


In [0]:
train = trainD_en
val = devD_en

##Print dataframes for all the data

>T1. Articles, Diagnostics/Procedures, train

>T2. Articles, Diagnostics/Procedures, dev

>T3. Articles, Diagnostics/Procedures, test

>T4. Articles, Diagnostics/Procedures, train, english

>T5. Articles, Diagnostics/Procedures, dev, english

>T6. Articles, Diagnostics/Procedures, test, english

>A1. Annotations, Diagnostics, train

>A2. Annotations, Diagnostics, dev

>A3. Annotations, Procedures, train

>A4. Annotations, Procedures, dev

>B1. Mapped_annotations, Diagnostics, train

>B2. Mapped_annotations, Diagnostics, dev

>B3. Mapped_annotations, Procedures, train

>B4. Mapped_annotations, Procedures, dev

>C1. Codes, Diagnostics

>C2. Codes, Procedures



In [8]:
print("- Print T1. Articles, Diagnostics/Procedures, train")
print(tabulate(df_train_articles.head(), headers='keys', tablefmt='psql'))

print("- Print T2. Articles, Diagnostics/Procedures, dev")
print(tabulate(df_dev_articles.head(), headers='keys', tablefmt='psql'))

#print("- Print T3. Articles, Diagnostics/Procedures, test")
#print(tabulate(df_test_articles.head(), headers='keys', tablefmt='psql'))

print("- Print T4. Articles, Diagnostics/Procedures, train, english")
print(tabulate(df_train_articles_en.head(), headers='keys', tablefmt='psql'))

print("- Print T5. Articles, Diagnostics/Procedures, dev, english")
print(tabulate(df_dev_articles_en.head(), headers='keys', tablefmt='psql'))

#print("- Print T6. Articles, Diagnostics/Procedures, test, english")
#print(tabulate(df_test_articles_en.head(), headers='keys', tablefmt='psql'))

print("- Print A1. Annotations, Diagnostics, train")
print(tabulate(df_train_annotationsD.head(), headers='keys', tablefmt='psql'))

print("- Print A2. Annotations, Diagnostics, dev")
print(tabulate(df_dev_annotationsD.head(), headers='keys', tablefmt='psql'))

print("- Print A3. Annotations, Procedures, train")
print(tabulate(df_train_annotationsP.head(), headers='keys', tablefmt='psql'))   

print("- Print A4. Annotations, Procedures, dev")
print(tabulate(df_dev_annotationsP.head(), headers='keys', tablefmt='psql'))

print("- Print B1. Mapped annotations, Diagnostics, train")
print(tabulate(df_trainD_annotations_mapping.head(), headers='keys', tablefmt='psql'))

print("- Print B2. Mapped annotations, Diagnostics, dev")
print(tabulate(df_devD_annotations_mapping.head(), headers='keys', tablefmt='psql'))

print("- Print B3. Mapped annotations, Procedures, train")
print(tabulate(df_trainP_annotations_mapping.head(), headers='keys', tablefmt='psql'))   

print("- Print B4. Mapped annotations, Procedures, dev")
print(tabulate(df_devP_annotations_mapping.head(), headers='keys', tablefmt='psql'))

print("- Print C1. Codes, Diagnostics")
print(tabulate(df_codeD.head(), headers='keys', tablefmt='psql'))

print("- Print C2. Codes, Procedures")
print(tabulate(df_codeP.head(), headers='keys', tablefmt='psql'))


- Print T1. Articles, Diagnostics/Procedures, train
+----+---------------------------+--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

NameError: ignored

#Create dictionary with codes

In [0]:
import collections

def Dict_tag_id_tag_mapping(df_code):
  tags_list = []
  for i in range (len(df_code['Code'])):
    tags_together = df_code['Code'][i]
    tags_together = tags_together.replace(']', '')
    tags_together = tags_together.replace('[', '')
    tags_together = tags_together.replace('\'', '')
    tags_separated = tags_together.split(', ')
    #print(tags_separated)
    for j in tags_separated:
      #print(j)
      tags_list.append(j)	  
  #print(tags_list)
  
  #Converting a list to dictionary with list elements as values in dictionary and keys are enumerated index starting from 0 i.e. index position of element in list
  dictOfTags = { tags_list[i] : i for i in range(0, len(tags_list) ) }
  print(dictOfTags)

  return(dictOfTags)


In [27]:
codeD_dict_tag_id_mapping = Dict_tag_id_tag_mapping(df_codeD)

{'A00.0': 0, 'A00.1': 1, 'A00.9': 2, 'A01': 3, 'A01.0': 4, 'A01.00': 5, 'A01.01': 6, 'A01.02': 7, 'A01.03': 8, 'A01.04': 9, 'A01.05': 10, 'A01.09': 11, 'A01.1': 12, 'A01.2': 13, 'A01.3': 14, 'A01.4': 15, 'A02': 16, 'A02.0': 17, 'A02.1': 18, 'A02.2': 19, 'A02.20': 20, 'A02.21': 21, 'A02.22': 22, 'A02.23': 23, 'A02.24': 24, 'A02.25': 25, 'A02.29': 26, 'A02.8': 27, 'A02.9': 28, 'A03': 29, 'A03.0': 30, 'A03.1': 31, 'A03.2': 32, 'A03.3': 33, 'A03.8': 34, 'A03.9': 35, 'A04': 36, 'A04.0': 37, 'A04.1': 38, 'A04.2': 39, 'A04.3': 40, 'A04.4': 41, 'A04.5': 42, 'A04.6': 43, 'A04.7': 44, 'A04.8': 45, 'A04.9': 46, 'A05': 47, 'A05.0': 48, 'A05.1': 49, 'A05.2': 50, 'A05.3': 51, 'A05.4': 52, 'A05.5': 53, 'A05.8': 54, 'A05.9': 55, 'A06': 56, 'A06.0': 57, 'A06.1': 58, 'A06.2': 59, 'A06.3': 60, 'A06.4': 61, 'A06.5': 62, 'A06.6': 63, 'A06.7': 64, 'A06.8': 65, 'A06.81': 66, 'A06.82': 67, 'A06.89': 68, 'A06.9': 69, 'A07': 70, 'A07.0': 71, 'A07.1': 72, 'A07.2': 73, 'A07.3': 74, 'A07.4': 75, 'A07.8': 76, 'A07.

In [28]:
codeP_dict_tag_id_mapping = Dict_tag_id_tag_mapping(df_codeP)

{'0016070': 0, '0016071': 1, '0016072': 2, '0016073': 3, '0016074': 4, '0016075': 5, '0016076': 6, '0016077': 7, '0016078': 8, '001607B': 9, '00160J0': 10, '00160J1': 11, '00160J2': 12, '00160J3': 13, '00160J4': 14, '00160J5': 15, '00160J6': 16, '00160J7': 17, '00160J8': 18, '00160JB': 19, '00160K0': 20, '00160K1': 21, '00160K2': 22, '00160K3': 23, '00160K4': 24, '00160K5': 25, '00160K6': 26, '00160K7': 27, '00160K8': 28, '00160KB': 29, '0016370': 30, '0016371': 31, '0016372': 32, '0016373': 33, '0016374': 34, '0016375': 35, '0016376': 36, '0016377': 37, '0016378': 38, '001637B': 39, '00163J0': 40, '00163J1': 41, '00163J2': 42, '00163J3': 43, '00163J4': 44, '00163J5': 45, '00163J6': 46, '00163J7': 47, '00163J8': 48, '00163JB': 49, '00163K0': 50, '00163K1': 51, '00163K2': 52, '00163K3': 53, '00163K4': 54, '00163K5': 55, '00163K6': 56, '00163K7': 57, '00163K8': 58, '00163KB': 59, '001U074': 60, '001U076': 61, '001U077': 62, '001U079': 63, '001U0J4': 64, '001U0J6': 65, '001U0J7': 66, '001

In [29]:
print(len(codeD_dict_tag_id_mapping))

98288


In [30]:
print(len(codeP_dict_tag_id_mapping))

87170


##Map annotated tags into tag_id 

In [0]:
def Create_transposed_list(list):
  #print("lenght and list are: ", len(list), "\t", list)
  np_list = np.asarray([list]).T
  #print("lenght and transposed token IOB list are: ", len(np_list), "\t", np_list)
  return(np_list)


def Create_mapped_tag_list(df_annotations, code_dict_tag_id_mapping):
  mapped_tag_list=[]
  for i in range(len(df_annotations)):
    t = df_annotations['ICD10-code'][i]    #to add '' : str = "\'" + t +  "\'" 
    upper = t.upper()
    #print(upper)
    mapping = code_dict_tag_id_mapping[upper]
    #print(mapping)
    #print("The code: ", upper, "\thas the mapping: ", mapping)
    mapped_tag_list.append(mapping)

  #Into numpy array
  np_mapped_tag_list =  Create_transposed_list(mapped_tag_list)      ##Nested function
  #print(np_mapped_tag_list)
  return(np_mapped_tag_list)

def Create_mapped_tag_dataframe(df_annotations, code_dict_tag_id_mapping, path):
  id_list = df_annotations['ArticleID']
  np_id_list =  Create_transposed_list(id_list)                      ##Nested function
  
  np_mapped_tag_list = Create_mapped_tag_list(df_annotations, code_dict_tag_id_mapping)        ##Nested function

  df = pd.DataFrame(columns=['article_id','mapped_tags'])
  for a in range(len(id_list)):
    df.loc[a] = [np.random.randint(0,2) for n in range(2)]
  for b in range(len(id_list)):
    df.loc[:, ['article_id']] = np_id_list
    df.loc[:, ['mapped_tags']] = np_mapped_tag_list
  print(tabulate(df.head(), headers= 'keys', tablefmt='psql'))

  df.to_csv(path, index=False)             #guardar dataframe como tsv sin el indice de la izquierda

  return(df)

In [0]:
path = path_codiesp + 'datasetv3/train/mapped_annotations/trainD_annotations_mapped'
print("- Save Mapped A1. Annotations, Diagnostics, train, dataframe in: ", path)
df_trainD_annotations_mapping =  Create_mapped_tag_dataframe(df_train_annotationsD, codeD_dict_tag_id_mapping, path) 

- Save Mapped A1. Annotations, Diagnostics, train, dataframe in:  /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/mapped_annotations/trainD_annotations_mapped
+----+---------------------------+---------------+
|    | article_id                |   mapped_tags |
|----+---------------------------+---------------|
|  0 | S0004-06142005000700014-1 |         23621 |
|  1 | S0004-06142005000700014-1 |         96956 |
|  2 | S0004-06142005000700014-1 |         29039 |
|  3 | S0004-06142005000700014-1 |         29009 |
|  4 | S0004-06142005000700014-1 |           181 |
+----+---------------------------+---------------+


In [0]:
path = path_codiesp + 'datasetv3/dev/mapped_annotations/devD_annotations_mapped'
print("- Save Mapped A2. Annotations, Diagnostics, dev, dataframe in: ", path)
df_devD_annotations_mapping =  Create_mapped_tag_dataframe(df_dev_annotationsD, codeD_dict_tag_id_mapping, path) 

- Save Mapped A2. Annotations, Diagnostics, dev, dataframe in:  /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/mapped_annotations/devD_annotations_mapped
+----+---------------------------+---------------+
|    | article_id                |   mapped_tags |
|----+---------------------------+---------------|
|  0 | S0004-06142005000900016-1 |         27975 |
|  1 | S0004-06142005000900016-1 |         23479 |
|  2 | S0004-06142005000900016-1 |         23560 |
|  3 | S0004-06142005000900016-1 |         28751 |
|  4 | S0004-06142005000900016-1 |         23453 |
+----+---------------------------+---------------+


In [0]:
path = path_codiesp + 'datasetv3/train/mapped_annotations/trainP_annotations_mapped'
print("- Save Mapped A4. Annotations, Procedures, dev, dataframe in: ", path)
df_trainP_annotations_mapping =  Create_mapped_tag_dataframe(df_train_annotationsP, codeP_dict_tag_id_mapping, path) 


path = path_codiesp + 'datasetv3/dev/mapped_annotations/devP_annotations_mapped'
print("- Save Mapped A4. Annotations, Procedures, dev, dataframe in: ", path)
df_devP_annotations_mapping =  Create_mapped_tag_dataframe(df_dev_annotationsP, codeP_dict_tag_id_mapping, path) 

- Save Mapped A4. Annotations, Procedures, dev, dataframe in:  /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/train/mapped_annotations/trainP_annotations_mapped
+----+---------------------------+---------------+
|    | article_id                |   mapped_tags |
|----+---------------------------+---------------|
|  0 | S0004-06142005000700014-1 |         71745 |
|  1 | S0004-06142005000700014-1 |         67183 |
|  2 | S0004-06142005000700014-1 |         71844 |
|  3 | S0004-06142005000700014-1 |         71740 |
|  4 | S0004-06142005000700014-1 |         86118 |
+----+---------------------------+---------------+
- Save Mapped A4. Annotations, Procedures, dev, dataframe in:  /content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/datasetv3/dev/mapped_annotations/devP_annotations_mapped
+----+---------------------------+---------------+
|    | article_id                |   mapped_tags |
|----+---------------------------+---------------|
|  0 | S0004-061420050

#Create dictionary with tags and frecuency

In [0]:
print("- Dict A1. Annotations, Diagnostics, train")
df_train_annotationsD

print("- Dict A2. Annotations, Diagnostics, dev")
df_dev_annotationsD

print("- Dict A3. Annotations, Procedures, train")
df_train_annotationsP   

print("- Dict A4. Annotations, Procedures, dev")
df_dev_annotationsP

- Dict A1. Annotations, Diagnostics, train
- Dict A2. Annotations, Diagnostics, dev
- Dict A3. Annotations, Procedures, train
- Dict A4. Annotations, Procedures, dev


ArticleID ICD10-code
0    S0004-06142005000900016-1    bt41zzz
1    S0004-06142005000900016-1       ct13
2    S0004-06142005001000011-1    3e1m39z
3    S0004-06142005001000011-1       0tcb
4    S0004-06142005001000011-1       bt02
..                         ...        ...
812  S2254-28842013000300009-1       5a1d
813  S2254-28842013000300009-1    3e1m39z
814  S2254-28842013000300009-1    bw03zzz
815  S2254-28842013000300009-1    bw00zzz
816  S2254-28842013000300009-1       bw20

[817 rows x 2 columns]

###Dict with tags frequency

In [0]:
#tag como list
"""tag2count = collections.defaultdict(lambda: 0)      #number of times that every tag in the list of tags appeas. default 0
for tags in y_train:
    #print(tags)
    for tag in tags:
        print(tag)
        tag2count[tag] += 1
        #print(tag2count[tag])
most_common_tags = sorted(tag2count.items(),
                          key=lambda x: x[1],
                          reverse=True)

print(most_common_tags)"""

In [32]:
import collections

def Dict_with_tags_frequency(df_annotations):
  #tag como string
  tag2count = collections.defaultdict(lambda: 0)      #number of times that every tag in the list of tags appeas. default 0
  for tags in df_annotations['ICD10-code']:
      #print(tags)
      for tag in tags.split():
      #for i in range (len(train['tags'])):
          #print(tag)
          #print(type(tag))
          t = tag.replace('\'', '')
          t = t.replace(']', '')
          t = t.replace('[', '')
          t = t.replace(',', '')
          #print(t)
          tag2count[t] += 1
          #print(tag2count[tag])
  most_common_tags = sorted(tag2count.items(),
                            key=lambda x: x[1],
                            reverse=True)

  print(most_common_tags)
  return(tag2count, most_common_tags)

trainD_tag2count, trainD_most_common_tags = Dict_with_tags_frequency(df_train_annotationsD)
devD_tag2count, devD_most_common_tags = Dict_with_tags_frequency(df_dev_annotationsD)
trainP_tag2count, trainP_most_common_tags = Dict_with_tags_frequency(df_train_annotationsP)
devP_tag2count, devP_most_common_tags = Dict_with_tags_frequency(df_dev_annotationsP)

[('r52', 112), ('r69', 99), ('r50.9', 97), ('i10', 77), ('r60.9', 66), ('r59.9', 65), ('r53.1', 57), ('r11.10', 47), ('r59.0', 46), ('r10.9', 46), ('r58', 45), ('b99.9', 45), ('d64.9', 43), ('e11.9', 41), ('i96', 37), ('r63.4', 34), ('r31.9', 34), ('n28.9', 30), ('b20', 30), ('l53.9', 30), ('r23.1', 29), ('d72.829', 28), ('f17.210', 28), ('t14.90', 27), ('r51', 26), ('t14.8', 26), ('b19.20', 26), ('k65.9', 24), ('r06.00', 24), ('n28.89', 23), ('l98.9', 23), ('r63.0', 22), ('k75.9', 22), ('l90.5', 20), ('n18.9', 20), ('i82.90', 19), ('e80.7', 19), ('r19.7', 19), ('m54.5', 18), ('r60.0', 18), ('b19.10', 18), ('r20.2', 18), ('r42', 17), ('r05', 17), ('r80.9', 17), ('b25.9', 17), ('c78.7', 16), ('i95.9', 16), ('r56.9', 16), ('c64.9', 15), ('j18.9', 15), ('f17.200', 15), ('i48.91', 15), ('c79.51', 15), ('k52.9', 15), ('l29.9', 15), ('r11.0', 15), ('f32.9', 14), ('a15.9', 14), ('f17.290', 14), ('r13.10', 14), ('m19.90', 14), ('r41.0', 14), ('e66.9', 14), ('r19.00', 13), ('j44.9', 13), ('r14.

In [33]:
trainD_most_common_tags

[('r52', 112),
 ('r69', 99),
 ('r50.9', 97),
 ('i10', 77),
 ('r60.9', 66),
 ('r59.9', 65),
 ('r53.1', 57),
 ('r11.10', 47),
 ('r59.0', 46),
 ('r10.9', 46),
 ('r58', 45),
 ('b99.9', 45),
 ('d64.9', 43),
 ('e11.9', 41),
 ('i96', 37),
 ('r63.4', 34),
 ('r31.9', 34),
 ('n28.9', 30),
 ('b20', 30),
 ('l53.9', 30),
 ('r23.1', 29),
 ('d72.829', 28),
 ('f17.210', 28),
 ('t14.90', 27),
 ('r51', 26),
 ('t14.8', 26),
 ('b19.20', 26),
 ('k65.9', 24),
 ('r06.00', 24),
 ('n28.89', 23),
 ('l98.9', 23),
 ('r63.0', 22),
 ('k75.9', 22),
 ('l90.5', 20),
 ('n18.9', 20),
 ('i82.90', 19),
 ('e80.7', 19),
 ('r19.7', 19),
 ('m54.5', 18),
 ('r60.0', 18),
 ('b19.10', 18),
 ('r20.2', 18),
 ('r42', 17),
 ('r05', 17),
 ('r80.9', 17),
 ('b25.9', 17),
 ('c78.7', 16),
 ('i95.9', 16),
 ('r56.9', 16),
 ('c64.9', 15),
 ('j18.9', 15),
 ('f17.200', 15),
 ('i48.91', 15),
 ('c79.51', 15),
 ('k52.9', 15),
 ('l29.9', 15),
 ('r11.0', 15),
 ('f32.9', 14),
 ('a15.9', 14),
 ('f17.290', 14),
 ('r13.10', 14),
 ('m19.90', 14),
 ('r41

In [34]:
trainD_tag2count


defaultdict(<function __main__.Dict_with_tags_frequency.<locals>.<lambda>>,
            {'n44.8': 4,
             'z20.818': 1,
             'r60.9': 66,
             'r52': 112,
             'a23.9': 9,
             'i83.90': 1,
             'i87.8': 2,
             'r50.9': 97,
             'n45.3': 3,
             'm25.50': 6,
             'd30.3': 1,
             'r58': 45,
             'r19.00': 13,
             'n50.9': 10,
             'd49.59': 11,
             'r63.4': 34,
             'n50.89': 7,
             'c63.10': 1,
             'g82.21': 1,
             'g71.8': 1,
             'r53.81': 9,
             'z98.85': 2,
             'g04.1': 1,
             'r20.1': 4,
             'k74.60': 5,
             'n32.9': 8,
             'g82.20': 6,
             'i85.00': 7,
             'i10': 77,
             'r53.1': 57,
             'b33.3': 1,
             'z96.0': 2,
             'r74.0': 11,
             'c22.0': 5,
             'k76.6': 6,
             'i85.01': 1,
   

####Translate Tags into Tag_ID

In [0]:
#y_list como string

def Dict_tag_id_tag_mapping(df_annotations):
  tags_list = []
  for i in range (len(df_annotations['ICD10-code'])):
    tags_together = df_annotations['ICD10-code'][i]
    tags_together = tags_together.replace(']', '')
    tags_together = tags_together.replace('[', '')
    tags_together = tags_together.replace('\'', '')
    tags_separated = tags_together.split(', ')
    #print(tags_separated)
    for j in tags_separated:
      #print(j)
      tags_list.append(j)	  
  #print(tags_list)
  
  #Converting a list to dictionary with list elements as values in dictionary and keys are enumerated index starting from 0 i.e. index position of element in list
  dictOfTags = { i : tags_list[i] for i in range(0, len(tags_list) ) }
  print(dictOfTags)

  return(dictOfTags)

trainD_tag_id_mapping = Dict_tag_id_tag_mapping(df_train_annotationsD)
devD_tag_id_mapping = Dict_tag_id_tag_mapping(df_dev_annotationsD)
trainP_tag_id_mapping = Dict_tag_id_tag_mapping(df_train_annotationsP)
devP_tag_id_mapping = Dict_tag_id_tag_mapping(df_dev_annotationsP)

{0: 'n44.8', 1: 'z20.818', 2: 'r60.9', 3: 'r52', 4: 'a23.9', 5: 'i83.90', 6: 'i87.8', 7: 'r50.9', 8: 'n45.3', 9: 'm25.50', 10: 'd30.3', 11: 'r58', 12: 'r19.00', 13: 'n50.9', 14: 'd49.59', 15: 'r63.4', 16: 'r52', 17: 'n50.89', 18: 'c63.10', 19: 'g82.21', 20: 'g71.8', 21: 'r53.81', 22: 'z98.85', 23: 'g04.1', 24: 'r20.1', 25: 'k74.60', 26: 'n32.9', 27: 'g82.20', 28: 'i85.00', 29: 'i10', 30: 'r53.1', 31: 'b33.3', 32: 'z96.0', 33: 'r74.0', 34: 'c22.0', 35: 'k76.6', 36: 'i85.01', 37: 'r18.8', 38: 'k70.30', 39: 'n32.0', 40: 'k40.90', 41: 'n32.89', 42: 'n28.89', 43: 'c78.7', 44: 'c77.9', 45: 'q61.3', 46: 'r59.9', 47: 'n28.9', 48: 'k31.7', 49: 'k56.60', 50: 'n13.9', 51: 'd64.9', 52: 'r18.8', 53: 'n13.30', 54: 'r18.0', 55: 'c80.0', 56: 'k59.00', 57: 'c16.9', 58: 'd50.9', 59: 'r63.0', 60: 'i10', 61: 'c64.9', 62: 'n13.8', 63: 'k44.9', 64: 'n80.9', 65: 'r19.00', 66: 'k66.0', 67: 'r50.9', 68: 'r10.2', 69: 'r31.9', 70: 'n85.8', 71: 'r58', 72: 'r53.81', 73: 'n28.89', 74: 'n80.9', 75: 'n80.8', 76: 'n23

In [0]:
#y_list como list
"""
tags_list = []
for i in range (len(train['tags'])):
  tags_together = train['tags'][i]
  #print(tags_together)
  #print(type(tags_together))
  for j in range(len(tags_together)):
    tags_one = tags_together[j]
    #print(tags_one)
    tags_list.append(tags_one)

print(tags_list)"""

In [0]:
#Converting a list to dictionary with list elements as values in dictionary and keys are enumerated index starting from 0 i.e. index position of element in list

dictOfTags = { i : tags_list[i] for i in range(0, len(tags_list) ) }

In [0]:
dictOfTgs = sorted(dictOfTags)

In [0]:
dictOfTags


{0: 'n44.8',
 1: 'z20.818',
 2: 'r60.9',
 3: 'r52',
 4: 'a23.9',
 5: 'i83.90',
 6: 'i87.8',
 7: 'r50.9',
 8: 'n45.3',
 9: 'm25.50',
 10: 'd30.3',
 11: 'r58',
 12: 'r19.00',
 13: 'n50.9',
 14: 'd49.59',
 15: 'r63.4',
 16: 'r52',
 17: 'n50.89',
 18: 'c63.10',
 19: 'g82.21',
 20: 'g71.8',
 21: 'r53.81',
 22: 'z98.85',
 23: 'g04.1',
 24: 'r20.1',
 25: 'k74.60',
 26: 'n32.9',
 27: 'g82.20',
 28: 'i85.00',
 29: 'i10',
 30: 'r53.1',
 31: 'b33.3',
 32: 'z96.0',
 33: 'r74.0',
 34: 'c22.0',
 35: 'k76.6',
 36: 'i85.01',
 37: 'r18.8',
 38: 'k70.30',
 39: 'n32.0',
 40: 'k40.90',
 41: 'n32.89',
 42: 'n28.89',
 43: 'c78.7',
 44: 'c77.9',
 45: 'q61.3',
 46: 'r59.9',
 47: 'n28.9',
 48: 'k31.7',
 49: 'k56.60',
 50: 'n13.9',
 51: 'd64.9',
 52: 'r18.8',
 53: 'n13.30',
 54: 'r18.0',
 55: 'c80.0',
 56: 'k59.00',
 57: 'c16.9',
 58: 'd50.9',
 59: 'r63.0',
 60: 'i10',
 61: 'c64.9',
 62: 'n13.8',
 63: 'k44.9',
 64: 'n80.9',
 65: 'r19.00',
 66: 'k66.0',
 67: 'r50.9',
 68: 'r10.2',
 69: 'r31.9',
 70: 'n85.8',
 71

In [0]:
print(len(dictOfTags))
#nltk.FreqDist(dictOfTags) 

5639


####Dict with Tag_id and frecuency

In [0]:
new_tag2count = {}
frequency_list=[]
for k,v in tag2count.items(): 
    #print ("%s -> %s" %(k,v))
    frequency_list.append(v)

In [0]:
new_tag2count = { i : frequency_list[i] for i in range(0, len(frequency_list)) }

In [0]:
new_tag2count

{0: 4,
 1: 1,
 2: 66,
 3: 112,
 4: 9,
 5: 1,
 6: 2,
 7: 97,
 8: 3,
 9: 6,
 10: 2,
 11: 9,
 12: 99,
 13: 2,
 14: 14,
 15: 41,
 16: 65,
 17: 23,
 18: 11,
 19: 9,
 20: 3,
 21: 9,
 22: 2,
 23: 15,
 24: 2,
 25: 5,
 26: 12,
 27: 11,
 28: 46,
 29: 9,
 30: 3,
 31: 37,
 32: 1,
 33: 45,
 34: 15,
 35: 11,
 36: 1,
 37: 2,
 38: 1,
 39: 28,
 40: 57,
 41: 17,
 42: 34,
 43: 22,
 44: 4,
 45: 3,
 46: 1,
 47: 13,
 48: 1,
 49: 2,
 50: 24,
 51: 29,
 52: 4,
 53: 10,
 54: 7,
 55: 1,
 56: 2,
 57: 30,
 58: 19,
 59: 11,
 60: 46,
 61: 1,
 62: 1,
 63: 9,
 64: 2,
 65: 1,
 66: 4,
 67: 5,
 68: 8,
 69: 6,
 70: 7,
 71: 77,
 72: 1,
 73: 2,
 74: 11,
 75: 5,
 76: 6,
 77: 1,
 78: 10,
 79: 2,
 80: 18,
 81: 1,
 82: 30,
 83: 5,
 84: 14,
 85: 26,
 86: 1,
 87: 22,
 88: 1,
 89: 6,
 90: 6,
 91: 1,
 92: 8,
 93: 8,
 94: 4,
 95: 10,
 96: 1,
 97: 16,
 98: 2,
 99: 16,
 100: 8,
 101: 7,
 102: 30,
 103: 2,
 104: 8,
 105: 3,
 106: 43,
 107: 9,
 108: 1,
 109: 4,
 110: 7,
 111: 9,
 112: 12,
 113: 1,
 114: 4,
 115: 47,
 116: 1,
 117: 4,
 1

#Output

Task 1 Diagnostics
- Spanish:

>J1.  df_train_annotated_articles_D : /datasetv3/train/articles_annotated/train_annotated_articles_D.csv

>J2.  df_dev_annotated_articles_D : /datasetv3/dev/articles_annotated/dev_annotated_articles_D.csv

- English:

>J3.  df_train_annotated_articles_en_D : /datasetv3/train/articles_annotated/train_annotated_articles_en_D.csv

>J4. df_dev_annotated_articles_en_D : /datasetv3/dev/articles_annotated/dev_annotated_articles_en_D.csv

Task 2 Procedures
- Spanish:

>J5. df_train_annotated_articles_P : /datasetv3/train/articles_annotated/train_annotated_articles_P.csv

>J6.  df_dev_annotated_articles_P : /datasetv3/dev/articles_annotated/dev_annotated_articles_P.csv


- English:

>J7. df_train_annotated_articles_en_P : /datasetv3/train/articles_annotated/train_annotated_articles_en_P.csv

>J8. df_dev_annotated_articles_en_P : /datasetv3/dev/articles_annotated/dev_annotated_articles_en_P.csv


##Text processing

In [0]:
##Import data Spanish, Diagnostics


def read_data(filename):
    data = pd.read_csv(filename, sep=',', usecols=["article_content", "tags"])
    #print(data['tags'])
    #print(data['article_content'])
    return data


path_codiesp='/content/drive/My Drive/Colab Notebooks/3. Codiesp/Codiespv2/'

print("- Read J3. Joined, Diagnostics, train, english")
train = read_data(path_codiesp + 'datasetv3/train/articles_annotated/train_annotated_articles_en_D.csv')
print("- Read J4. Joined, Diagnostics, dev, english")
val = read_data(path_codiesp + 'datasetv3/dev/articles_annotated/dev_annotated_articles_en_D.csv')

print('Shape of data')
print(f'Train: {train.shape}')
print(f'Validation: {val.shape}')



- Read J3. Joined, Diagnostics, train, english
- Read J4. Joined, Diagnostics, dev, english
Shape of data
Train: (500, 2)
Validation: (250, 2)


###Dataframes to X_train, X_val, y_train and y_val

In [0]:
X_train = train.article_content.values  
y_train = train.tags.values
X_val = val.article_content.values
y_val =  val.tags.values

In [36]:
print(train)
print(type(train)) #pandas.core.series

print(train.tags)
print(type(train.tags)) #pandas.core.series

print(train.tags.values)
print(type(train.tags.values))   #numpy.ndarray [list(['n44.8', 'z20.818', 'r60.9', 'r52', 'a23.9', 'i83.90', 'i87.8', 'r50.9', 'n45.3', 'm25.50'])

print(type(X_train)) #numpy.ndarray

                                       article_content                                               tags
0    We describe the case of a 37-year-old man with...  [23621, 96956, 29039, 29009, 181, 12233, 12306...
1    A 73-year-old male presented at our department...  [28634, 10884, 29081, 13491, 5270, 4167, 29035...
2    We report the case of a 29-year-old woman who ...                                      [3086, 29031]
3    A 43-year-old man, an active smoker of about 1...  [28557, 28527, 1437, 29277, 1476, 1389, 5258, ...
4    A 36-year-old male, with no relevant past medi...    [28595, 23697, 3325, 29054, 29009, 23696, 1918]
..                                                 ...                                                ...
495  A 72-year-old male in HD program from December...  [23441, 13423, 1291, 1250, 13525, 11998, 29027...
496  A 53-year-old patient at the time of diagnosis...  [2102, 2107, 1755, 2111, 1928, 3324, 2112, 470...
497  A 33-year-old woman presented to the emer

In [41]:
help(ast.literal_eval)

train.tags = train.tags.apply(ast.literal_eval)

val.tags = val.tags.apply(ast.literal_eval)

Help on function literal_eval in module ast:

literal_eval(node_or_string)
    Safely evaluate an expression node or a string containing a Python
    expression.  The string or node provided may only consist of the following
    Python literal structures: strings, bytes, numbers, tuples, lists, dicts,
    sets, booleans, and None.



In [42]:
print(y_train)
#print(type(y_train))   #numpy.ndarray

[list([23621, 96956, 29039, 29009, 181, 12233, 12306, 29007, 23625, 17743])
 list([28634, 10884, 29081, 13491, 5270, 4167, 29035, 23479, 11056, 2110, 3330, 29277, 11559, 1928, 2127, 1926, 1898, 3325, 29033, 10893, 2113, 12327])
 list([3086, 29031])
 list([28557, 28527, 1437, 29277, 1476, 1389, 5258, 29012, 28929, 29054, 29050, 4852, 13529, 2136, 28595, 13426, 28541, 13546, 28648, 13490])
 list([28595, 23697, 3325, 29054, 29009, 23696, 1918])
 list([28933, 14216, 4717, 28554, 28555])
 list([6427, 6379, 29015, 98270, 5781, 28625, 13611, 23518, 6426, 12239, 10762, 29012, 887, 98182, 29096, 1413, 13630, 12240, 28592, 13566])
 list([824, 129, 830, 14140, 12327, 98, 29033, 29081, 29009, 827, 49327, 13622, 14216, 29035])
 list([23511, 13221, 23517])
 list([97748, 29019, 4855, 5258, 11026, 29337, 27662, 29025, 28463, 29007])
 list([23479, 2121, 2107, 27966, 29035, 23480, 13179, 13434, 23414, 3447, 28592, 23397, 28591, 2158, 13478, 1386, 3337, 29050, 10762, 1928, 23413])
 list([28555, 29147, 29

###Text processing

In [0]:
def clean_text(text):
    text = text.strip().lower()
    text = re.sub('[/(){}\[\]\|@,;]', ' ', text)
    text = re.sub('[^0-9a-z #+_]', '', text)
    text = ' '.join([word for word in str(text).split() if word not in set(stopwords.words('english'))])
    return text

X_train = [clean_text(text) for text in train.article_content]  #X_train = [clean_text(text) for text in X_train]
X_val = [clean_text(text) for text in val.article_content]  #X_val = [clean_text(text) for text in X_val]


In [0]:
"""REPLACE_BY_SPACE_RE = re.compile('[/(){}\[\]\|@,;]')
BAD_SYMBOLS_RE = re.compile('[^0-9a-z #+_]')
STOPWORDS = set(stopwords.words('english'))

def text_prepare(text):
    #text: a string     
    #return: modified initial string
  
    text = text.lower() # lowercase text
    text = REPLACE_BY_SPACE_RE.sub(' ', text) # replace REPLACE_BY_SPACE_RE symbols by space in text
    text = BAD_SYMBOLS_RE.sub('', text) # delete symbols which are in BAD_SYMBOLS_RE from text
    text =  ' '.join([w for w in text.split() if not w in STOPWORDS]) # delete stopwords from text
    return text
"""

"""def cleanText(text):
    text=str(text).lower()
    #tokeniza the text
    tokens=word_tokenize(text)
    #remove the stopwords
    tokens = [word for word in tokens if word not in stopwords_en]    
    #(4) obtain the stems
    tokens = [PorterStemmer().stem(word) for word in tokens] 
   #(5) finally, remove words with len <3 and words that contain numbers, puntuaction, ect
    min_length = 3
    p = re.compile('[a-zA-Z]+');
    filtered_tokens=[]
    for token in tokens:
        if len(token)>=min_length and p.match(token):
            filtered_tokens.append(token)
            
    return filtered_tokens"""

"""aux=train.article_content
for text in aux:
  #print(text)
  print(clean_text(text))
  print("---------------------------------")

aux=validation.article_content
for text in aux:
  #print(text)
  print(clean_text(text))
  print("---------------------------------")"""

In [0]:
print(type(X_train)) #list ['describe case 37yearold man previous active life com...

print(X_train)
for i in X_train:
  print(i, "\n")

<class 'list'>
['describe case 37yearold man previous active life complained osteoarticular pain variable location last month fever last week peaks morning evening 40 cbefore onset symptoms extremadura endemic region brucella taking pasteurized milk cheese cattleamong diners appeared several cases brucellosisduring admission study febrile syndrome epidemiological history possible exposure brucella presents picture right orchiepididymitisphysical examination revealed ta 402 c ta 109 68 mmhg fc 105 bpmshe conscious oriented sweating eupneic good nutritional status hydrationadenopathy goiter jugular vein engorgement symmetrical carotid pulses present head neckauscultation cardiac arrhythmia murmurs ropes extractspulmonary emphysema vesicular murmur conservationabdomen blade depressible without masses enlargementneurological examination revealed meningeal signs focality dataextremities without varices edemasperipheral peace present symmetricalurological examination revealed enlarged right 

In [0]:
print(type(X_val)) #list ['describe case 37yearold man previous active life com...

print(X_val)
for i in X_val:
  print(i, "\n")

<class 'list'>
['29yearold woman history duodenal ulcer constipation complaining pain right renal fossa compatible renoureteral crisisno history nephrolithiasis hematuria urinary tract infectionsthe examination revealed positive right renal percussionultrasound showed right foot local ectasia thinning parenchymathe uiv shows functional annulation right renal unit rest examination normala retrograde pyelography showed stenosis right pyeloureteral junction negative right ureter urine cytologyto perform reconstructive surgery exeresis performed renal scintigraphy showing relative uptake 33 right kidney 67 left kidney1right renal pyeloplasty performed according andhynes techniquethe anatomopathological examination stenosis urinary tract revealed vesicular hemangioma cause obstruction allow passage cannulapostoperative urography 3 months showed uptake right renal elimination contrast slight delay compared left kidney1the patient discharged outpatient clinic three years surgery two controls 

In [0]:
X_train[:1]

['describe case 37yearold man previous active life complained osteoarticular pain variable location last month fever last week peaks morning evening 40 cbefore onset symptoms extremadura endemic region brucella taking pasteurized milk cheese cattleamong diners appeared several cases brucellosisduring admission study febrile syndrome epidemiological history possible exposure brucella presents picture right orchiepididymitisphysical examination revealed ta 402 c ta 109 68 mmhg fc 105 bpmshe conscious oriented sweating eupneic good nutritional status hydrationadenopathy goiter jugular vein engorgement symmetrical carotid pulses present head neckauscultation cardiac arrhythmia murmurs ropes extractspulmonary emphysema vesicular murmur conservationabdomen blade depressible without masses enlargementneurological examination revealed meningeal signs focality dataextremities without varices edemasperipheral peace present symmetricalurological examination revealed enlarged right test attached s

In [46]:
X_val[:1]

['29yearold woman history duodenal ulcer constipation complaining pain right renal fossa compatible renoureteral crisisno history nephrolithiasis hematuria urinary tract infectionsthe examination revealed positive right renal percussionultrasound showed right foot local ectasia thinning parenchymathe uiv shows functional annulation right renal unit rest examination normala retrograde pyelography showed stenosis right pyeloureteral junction negative right ureter urine cytologyto perform reconstructive surgery exeresis performed renal scintigraphy showing relative uptake 33 right kidney 67 left kidney1right renal pyeloplasty performed according andhynes techniquethe anatomopathological examination stenosis urinary tract revealed vesicular hemangioma cause obstruction allow passage cannulapostoperative urography 3 months showed uptake right renal elimination contrast slight delay compared left kidney1the patient discharged outpatient clinic three years surgery two controls performed urolo

##Label processing of Train 

####Count words and tags

In [47]:
word2count = collections.defaultdict(lambda: 0)         #number of times that every word of the vocabulary appears. default 0.


for text in X_train:
    #print(text)
    #print(type(text))
    for word in text.split():    #split() if word is a string to divide between words, not character
        #print(word)
        #print(word2count[word])
        word2count[word] += 1

most_common_words = sorted(word2count.items(),
                          key=lambda x: x[1],
                          reverse=True)

print(most_common_words)

[('patient', 1383), ('showed', 692), ('left', 606), ('right', 588), ('performed', 587), ('treatment', 571), ('mg', 570), ('without', 497), ('examination', 425), ('normal', 413), ('history', 398), ('months', 379), ('pain', 336), ('due', 334), ('cm', 322), ('tumor', 305), ('study', 303), ('revealed', 301), ('days', 300), ('diagnosis', 292), ('dl', 278), ('presented', 258), ('renal', 257), ('day', 254), ('abdominal', 232), ('lesion', 227), ('observed', 223), ('clinical', 217), ('years', 217), ('mass', 216), ('2', 215), ('surgery', 212), ('1', 207), ('3', 201), ('hours', 199), ('eye', 199), ('two', 193), ('later', 193), ('g', 190), ('l', 190), ('ct', 188), ('negative', 188), ('blood', 185), ('male', 184), ('lower', 183), ('ml', 181), ('10', 180), ('presence', 180), ('diagnosed', 178), ('admission', 174), ('one', 172), ('decided', 167), ('emergency', 164), ('surgical', 163), ('ultrasound', 162), ('4', 162), ('lesions', 162), ('treated', 161), ('department', 159), ('tests', 156), ('positive'

In [49]:
#tag como list
tag2count = collections.defaultdict(lambda: 0)      #number of times that every tag in the list of tags appeas. default 0
for tags in y_train:
    #print(tags)
    for tag in tags:
        print(tag)
        tag2count[tag] += 1
        #print(tag2count[tag])
most_common_tags = sorted(tag2count.items(),
                          key=lambda x: x[1],
                          reverse=True)

print(most_common_tags)

Se han truncado las últimas 5000 líneas del flujo de salida.
23435
11008
3465
10768
11992
13787
13423
23440
10893
11945
13788
28626
13183
11918
28522
23696
23621
23695
29007
27429
23614
1413
20984
29054
28586
13787
17761
29031
13635
29081
2142
98055
818
13788
13121
6807
7139
28629
6463
29009
2117
28628
10762
12582
12542
1898
9434
29008
9748
9424
9702
2142
9643
13550
13434
29035
12655
12611
13131
13513
3325
98127
29081
28509
13259
3512
28531
20176
23692
1244
23625
3447
4683
4701
23577
181
3061
18747
1245
13874
1291
29009
28524
82114
28555
1240
13935
311
13386
28621
29054
1928
23479
1898
29033
98071
3229
2372
29035
1042
11012
3625
5252
1075
13707
4717
4683
28589
14131
830
705
1284
547
836
98
97878
13741
13702
181
29147
13742
13731
23400
3315
1551
69514
29031
29009
29081
39511
23678
2156
1898
1386
1894
98055
2121
28527
13529
23672
11990
29081
29033
29009
12164
5270
23674
5258
5775
13546
13521
13430
13540
13550
28554
29007
28555
4826
28746
28075
23479
23471
23470
1927
29035
28751
69514
867

In [48]:
#tag como string
"""
tag2count = collections.defaultdict(lambda: 0)      #number of times that every tag in the list of tags appeas. default 0
for tags in y_train:
    #print(tags)
    for tag in tags.split():
    #for i in range (len(train['tags'])):
        #print(tag)
        #print(type(tag))
        t = tag.replace('\'', '')
        t = t.replace(']', '')
        t = t.replace('[', '')
        t = t.replace(',', '')
        #print(t)
        tag2count[t] += 1
        #print(tag2count[tag])
most_common_tags = sorted(tag2count.items(),
                          key=lambda x: x[1],
                          reverse=True)

print(most_common_tags)"""

AttributeError: ignored

In [50]:
most_common_tags

[(29009, 112),
 (29081, 99),
 (29007, 97),
 (10762, 77),
 (29039, 66),
 (29035, 65),
 (29012, 57),
 (28559, 47),
 (29033, 46),
 (28555, 46),
 (29031, 45),
 (1291, 45),
 (3447, 43),
 (4167, 41),
 (12327, 37),
 (29054, 34),
 (28751, 34),
 (14216, 30),
 (830, 30),
 (23480, 30),
 (28648, 29),
 (5258, 28),
 (3512, 28),
 (69514, 27),
 (827, 26),
 (69512, 26),
 (29008, 26),
 (13546, 24),
 (28484, 24),
 (23479, 23),
 (14781, 23),
 (29050, 22),
 (13622, 22),
 (14585, 20),
 (23440, 20),
 (4717, 19),
 (28621, 19),
 (12164, 19),
 (824, 18),
 (18709, 18),
 (28626, 18),
 (29037, 18),
 (28929, 17),
 (28481, 17),
 (836, 17),
 (29142, 17),
 (29025, 16),
 (2121, 16),
 (12326, 16),
 (1928, 15),
 (28557, 15),
 (13386, 15),
 (12510, 15),
 (5252, 15),
 (11012, 15),
 (2142, 15),
 (14131, 15),
 (5270, 14),
 (98, 14),
 (28912, 14),
 (5473, 14),
 (28569, 14),
 (4486, 14),
 (16913, 14),
 (28595, 13),
 (12611, 13),
 (97958, 13),
 (28576, 13),
 (29030, 13),
 (4689, 13),
 (1898, 12),
 (3337, 12),
 (3315, 12),
 (311

In [51]:
print(tag2count)
print(tag2count.keys())
print(tag2count.values())

defaultdict(<function <lambda> at 0x7f8726657598>, {23621: 4, 96956: 1, 29039: 66, 29009: 112, 181: 9, 12233: 1, 12306: 2, 29007: 97, 23625: 3, 17743: 6, 28634: 2, 10884: 9, 29081: 99, 13491: 2, 5270: 14, 4167: 41, 29035: 65, 23479: 23, 11056: 11, 2110: 9, 3330: 3, 29277: 9, 11559: 2, 1928: 15, 2127: 2, 1926: 5, 1898: 12, 3325: 11, 29033: 46, 10893: 9, 2113: 3, 12327: 37, 3086: 1, 29031: 45, 28557: 15, 28527: 11, 1437: 1, 1476: 2, 1389: 1, 5258: 28, 29012: 57, 28929: 17, 29054: 34, 29050: 22, 4852: 4, 13529: 3, 2136: 1, 28595: 13, 13426: 1, 28541: 2, 13546: 24, 28648: 29, 13490: 4, 23697: 10, 23696: 7, 1918: 1, 28933: 2, 14216: 30, 4717: 19, 28554: 11, 28555: 46, 6427: 1, 6379: 1, 29015: 9, 98270: 2, 5781: 1, 28625: 4, 13611: 5, 23518: 8, 6426: 6, 12239: 7, 10762: 77, 887: 1, 98182: 2, 29096: 11, 1413: 5, 13630: 6, 12240: 1, 28592: 10, 13566: 2, 824: 18, 129: 1, 830: 30, 14140: 5, 98: 14, 827: 26, 49327: 1, 13622: 22, 23511: 1, 13221: 6, 23517: 6, 97748: 1, 29019: 8, 4855: 8, 11026: 4,

####Dict with Tag_id and frecuency

In [0]:
new_tag2count = {}
frequency_list=[]
for k,v in tag2count.items(): 
    #print ("%s -> %s" %(k,v))
    frequency_list.append(v)

In [0]:
new_tag2count = { i : frequency_list[i] for i in range(0, len(frequency_list)) }

In [0]:
new_tag2count

{0: 4,
 1: 1,
 2: 66,
 3: 112,
 4: 9,
 5: 1,
 6: 2,
 7: 97,
 8: 3,
 9: 6,
 10: 2,
 11: 9,
 12: 99,
 13: 2,
 14: 14,
 15: 41,
 16: 65,
 17: 23,
 18: 11,
 19: 9,
 20: 3,
 21: 9,
 22: 2,
 23: 15,
 24: 2,
 25: 5,
 26: 12,
 27: 11,
 28: 46,
 29: 9,
 30: 3,
 31: 37,
 32: 1,
 33: 45,
 34: 15,
 35: 11,
 36: 1,
 37: 2,
 38: 1,
 39: 28,
 40: 57,
 41: 17,
 42: 34,
 43: 22,
 44: 4,
 45: 3,
 46: 1,
 47: 13,
 48: 1,
 49: 2,
 50: 24,
 51: 29,
 52: 4,
 53: 10,
 54: 7,
 55: 1,
 56: 2,
 57: 30,
 58: 19,
 59: 11,
 60: 46,
 61: 1,
 62: 1,
 63: 9,
 64: 2,
 65: 1,
 66: 4,
 67: 5,
 68: 8,
 69: 6,
 70: 7,
 71: 77,
 72: 1,
 73: 2,
 74: 11,
 75: 5,
 76: 6,
 77: 1,
 78: 10,
 79: 2,
 80: 18,
 81: 1,
 82: 30,
 83: 5,
 84: 14,
 85: 26,
 86: 1,
 87: 22,
 88: 1,
 89: 6,
 90: 6,
 91: 1,
 92: 8,
 93: 8,
 94: 4,
 95: 10,
 96: 1,
 97: 16,
 98: 2,
 99: 16,
 100: 8,
 101: 7,
 102: 30,
 103: 2,
 104: 8,
 105: 3,
 106: 43,
 107: 9,
 108: 1,
 109: 4,
 110: 7,
 111: 9,
 112: 12,
 113: 1,
 114: 4,
 115: 47,
 116: 1,
 117: 4,
 1

##Apply Multilabel binarizer with Tag_id

In [0]:
from sklearn.preprocessing import MultiLabelBinarizer

multilabel_binarizer = MultiLabelBinarizer()
multilabel_binarizer.fit(train['tags'])

# transform target variable
y = multilabel_binarizer.transform(train['tags'])

In [0]:
print(new_tag2count.keys())

dict_keys([0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219,

In [52]:
%%time

mlb = MultiLabelBinarizer(classes=sorted(tag2count.keys()))
y_train = mlb.fit_transform(y_train)
y_val = mlb.fit_transform(y_val)

print(f'y_train shape: {y_train.shape}')
print(f'y_val shape: {y_val.shape}')

y_train shape: (500, 1767)
y_val shape: (250, 1767)
CPU times: user 11.4 ms, sys: 2.94 ms, total: 14.3 ms
Wall time: 17.1 ms


/usr/local/lib/python3.6/dist-packages/sklearn/preprocessing/_label.py:987: UserWarning: unknown class(es) [10131, 1064, 10784, 10810, 1090, 10933, 10964, 10979, 10987, 10991, 11083, 11086, 11191, 11223, 11250, 11263, 11560, 11565, 1177, 11860, 11867, 11871, 11916, 11926, 11927, 11940, 1197, 12389, 12456, 12502, 12534, 1254, 12552, 12553, 12684, 12709, 12783, 12791, 12830, 12842, 12878, 12885, 12922, 12929, 13023, 13028, 1305, 13074, 13086, 13156, 1323, 1328, 13288, 1334, 13412, 13425, 13436, 1344, 13443, 13450, 13501, 13506, 13518, 13528, 13544, 13715, 13760, 13926, 1395, 13957, 14142, 14244, 14395, 1456, 14608, 1467, 15110, 1522, 1535, 15397, 1545, 1602, 1603, 1641, 16802, 16830, 16974, 1737, 17731, 17755, 17806, 17885, 17914, 17936, 17942, 17973, 18036, 18039, 18279, 18399, 18634, 18635, 18662, 18666, 18702, 1872, 1897, 1917, 1934, 1935, 1991, 20022, 20023, 2004, 20146, 2015, 20172, 20202, 2100, 2101, 21106, 2118, 2145, 2174, 21971, 22147, 2229, 22411, 22891, 23073, 23078, 23086, 23

In [53]:
print(y_val)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 1 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


##Vectorization of Diagnostics, english

In [0]:
VOCAB_SIZE = 5000

WORD2INDEX = {token[0]: i
              for i, token in enumerate(most_common_words[:VOCAB_SIZE])}
INDEX2WORD = {v: k for k, v in WORD2INDEX.items()}




In [0]:
def get_bow(text, word2index=WORD2INDEX, vocab_size=VOCAB_SIZE):
    vect = np.zeros(vocab_size)
    for word in text.split():
        if word in word2index:
            vect[word2index[word]] += 1
    return vect



In [56]:
X_train_bow = sp.sparse.vstack([sp.sparse.csr_matrix(get_bow(text))
                                for text in tqdm.tqdm(X_train)])
X_val_bow = sp.sparse.vstack([sp.sparse.csr_matrix(get_bow(text))
                               for text in tqdm.tqdm(X_val)])

print('\nX_train_bow shape:', X_train_bow.shape)
print('X_val_bow shape:', X_val_bow.shape)




100%|██████████| 250/250 [00:00<00:00, 2807.92it/s]



X_train_bow shape: (500, 5000)
X_val_bow shape: (250, 5000)


In [0]:
from sklearn.feature_extraction.text import TfidfVectorizer


In [58]:
%%time
tfidf_vectorizer = TfidfVectorizer(token_pattern='\S+',
                                   min_df=5, max_df=0.9,
                                   ngram_range=(1, 2))
tfidf_vectorizer.fit(X_train)

X_train_tfidf = tfidf_vectorizer.transform(X_train)
X_val_tfidf = tfidf_vectorizer.transform(X_val)

print('X_train_tfidf shape:', X_train_tfidf.shape)
print('X_val_tfidf shape:', X_val_tfidf.shape)

X_train_tfidf shape: (500, 3694)
X_val_tfidf shape: (250, 3694)
CPU times: user 471 ms, sys: 9.75 ms, total: 481 ms
Wall time: 492 ms


In [0]:
def train_model(clf, X_tr, y_tr, params=None):
    if params is None:
        model = OneVsRestClassifier(estimator=clf)
        model.fit(X_tr, y_tr)
        return model
    else:
        params = {f'estimator__{k}': v for k, v in params.items()}
        # print(params)
        gs = GridSearchCV(OneVsRestClassifier(estimator=clf),
                          param_grid=params, cv=5,
                          scoring=make_scorer(f1_score,
                                              average='weighted'),
                          verbose=10, n_jobs=-1)
        gs.fit(X_tr, y_tr)
        print(f'Best CV score: {gs.best_score_:.5f}')
        return gs.best_estimator_


In [0]:
SEED = 78
lr_params = {
    'C': [0.1, 1, 5, 10],
    'penalty': ['l1', 'l2'],
    'random_state': [SEED],
    'max_iter': [1000]
}

In [61]:
print(y_train)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


In [0]:
import warnings
warnings.filterwarnings('ignore')

In [62]:
print(y_train)

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


In [63]:
%%time
clf_bow = train_model(LogisticRegression(),
                      X_tr=X_train_bow,
                      y_tr=y_train,
                      params=lr_params)



Fitting 5 folds for each of 8 candidates, totalling 40 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 tasks      | elapsed:    0.9s
[Parallel(n_jobs=-1)]: Done   4 tasks      | elapsed:    1.1s
[Parallel(n_jobs=-1)]: Done   9 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done  14 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done  21 tasks      | elapsed:  5.0min
[Parallel(n_jobs=-1)]: Done  28 tasks      | elapsed:  7.3min
[Parallel(n_jobs=-1)]: Done  37 tasks      | elapsed:  9.7min
[Parallel(n_jobs=-1)]: Done  40 out of  40 | elapsed: 11.0min finished


Best CV score: 0.07019
CPU times: user 58.1 s, sys: 117 ms, total: 58.2 s
Wall time: 11min 55s


In [64]:
clf_bow


OneVsRestClassifier(estimator=LogisticRegression(C=10, class_weight=None,
                                                 dual=False, fit_intercept=True,
                                                 intercept_scaling=1,
                                                 l1_ratio=None, max_iter=1000,
                                                 multi_class='auto',
                                                 n_jobs=None, penalty='l2',
                                                 random_state=78,
                                                 solver='lbfgs', tol=0.0001,
                                                 verbose=0, warm_start=False),
                    n_jobs=None)

In [74]:
%%time
clf_tfidf = train_model(LogisticRegression(),
                        X_tr=X_train_tfidf,
                        y_tr=y_train,
                        params=lr_params)

Fitting 5 folds for each of 8 candidates, totalling 40 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 2 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 tasks      | elapsed:    0.8s
[Parallel(n_jobs=-1)]: Done   4 tasks      | elapsed:    0.9s
[Parallel(n_jobs=-1)]: Done   9 tasks      | elapsed:   58.0s
[Parallel(n_jobs=-1)]: Done  14 tasks      | elapsed:   58.5s
[Parallel(n_jobs=-1)]: Done  21 tasks      | elapsed:  2.4min
[Parallel(n_jobs=-1)]: Done  28 tasks      | elapsed:  3.5min
[Parallel(n_jobs=-1)]: Done  37 tasks      | elapsed:  4.7min
[Parallel(n_jobs=-1)]: Done  40 out of  40 | elapsed:  5.4min finished


Best CV score: 0.01538
CPU times: user 29.9 s, sys: 185 ms, total: 30.1 s
Wall time: 5min 51s


In [77]:
clf_tfidf

OneVsRestClassifier(estimator=LogisticRegression(C=10, class_weight=None,
                                                 dual=False, fit_intercept=True,
                                                 intercept_scaling=1,
                                                 l1_ratio=None, max_iter=1000,
                                                 multi_class='auto',
                                                 n_jobs=None, penalty='l2',
                                                 random_state=78,
                                                 solver='lbfgs', tol=0.0001,
                                                 verbose=0, warm_start=False),
                    n_jobs=None)

In [78]:
y_pred_bow = clf_bow.predict(X_val_bow)
y_pred_tfidf = clf_tfidf.predict(X_val_tfidf)

f1_score_bow = f1_score(y_val, y_pred_bow, average='weighted')
f1_score_tfidf = f1_score(y_val, y_pred_tfidf, average='weighted')

print(f'LR + BOW - F1 score: {f1_score_bow:.5f}')
print(f'LR + TF-IDF - F1 score: {f1_score_tfidf:.5f}')

LR + BOW - F1 score: 0.09969
LR + TF-IDF - F1 score: 0.03695


/usr/local/lib/python3.6/dist-packages/sklearn/metrics/_classification.py:1515: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no true nor predicted samples. Use `zero_division` parameter to control this behavior.
  average, "true nor predicted", 'F-score is', len(true_sum)


In [66]:
print(X_val_bow)

  (0, 0)	1.0
  (0, 1)	3.0
  (0, 2)	2.0
  (0, 3)	8.0
  (0, 4)	4.0
  (0, 8)	3.0
  (0, 10)	2.0
  (0, 11)	1.0
  (0, 12)	1.0
  (0, 17)	2.0
  (0, 22)	6.0
  (0, 28)	2.0
  (0, 31)	2.0
  (0, 33)	1.0
  (0, 36)	1.0
  (0, 41)	1.0
  (0, 60)	1.0
  (0, 85)	1.0
  (0, 90)	1.0
  (0, 114)	1.0
  (0, 116)	1.0
  (0, 122)	1.0
  (0, 146)	1.0
  (0, 160)	1.0
  (0, 176)	1.0
  :	:
  (249, 1370)	1.0
  (249, 1371)	1.0
  (249, 1423)	1.0
  (249, 1722)	1.0
  (249, 1749)	1.0
  (249, 1800)	1.0
  (249, 1925)	1.0
  (249, 2046)	1.0
  (249, 2069)	1.0
  (249, 2114)	1.0
  (249, 2554)	1.0
  (249, 2611)	1.0
  (249, 2626)	1.0
  (249, 2742)	1.0
  (249, 2859)	1.0
  (249, 2862)	1.0
  (249, 3081)	1.0
  (249, 3226)	1.0
  (249, 3525)	1.0
  (249, 3693)	4.0
  (249, 4081)	1.0
  (249, 4095)	1.0
  (249, 4131)	1.0
  (249, 4508)	2.0
  (249, 4624)	1.0


In [79]:
for idx in np.random.randint(0, len(val), size=10):
    x_val_bow = X_val_bow[idx].reshape(1, -1)
    x_val_tfidf = X_val_tfidf[idx].reshape(1, -1)
    y_pred_tags_bow = mlb.inverse_transform(clf_bow.predict(x_val_bow))
    y_pred_tags_tfidf = mlb.inverse_transform(clf_tfidf.predict(x_val_tfidf))
   # print('Content: \t', val.title.iloc[idx])
   # print('\tTrue tags: \t\t', ', '.join(val.tags.iloc[idx]))
   # print('\tBoW pred tags: \t\t', ', '.join(y_pred_tags_bow[0]))
   # print('\tTF-IDF pred tags: \t', ', '.join(y_pred_tags_tfidf[0]))


    print('Content: \t', val.article_content.iloc[idx])
    #print('\tTrue tags: \t\t', ', '.join(val.tags.iloc[idx]))
    print(val.tags.iloc[idx])
    #print(x_val_bow)
    print(y_pred_tags_bow)
    print(y_pred_tags_tfidf)
    #print("tf", x_val_tfidf)
    #print('\tBoW pred tags: \t\t', ', '.join(y_pred_tags_bow[0]))
    print('====================================================')

Content: 	 A 13-year-old boy was referred for evaluation after suffering an ocular trauma in his left eye with a straps.
Visual acuity was 20/20 in both eyes.
The examination of the right eye was normal and, in the left eye, a microhyphema and anterior uveitis were observed.
A dilated fundus examination of the left eye showed rounded equatorial hemorrhages in the left eye.
Intraocular pressure values were normal (15 mmHg and 12 mmHg, respectively).
The patient developed inferior peripheral ischemia (demonstrated by GPA) three weeks after the trauma (at this time the patient had a superior temporal peripheral scotoma) with later development, twelve months later, of neovascularization.
Complete hematologic study and blood coagulation tests were normal.
The result of the sickle cell disease test was also negative.
Microhyphema and nonsteroidal anti-inflammatory drugs (NSAIDs) were managed with gradual resolution of steroid secretion (1% atropine and topical steroids), eye protection for o